In [1]:
import roboidai as ai
import cv2
from ultralytics import YOLO
import yaml
import os
!pwd 
# Train Setting
train_mode = False
image_size = 1280
epoch = 10
batch_size = 8
train_data = os.getcwd() + '/dataset/data.yaml'
#'/home/yumjunstar/Desktop/YJW/dataset/data.yaml'

# Target Camera
camera_target = 'ip0'

# Load label list
all_child_names = [] # 모든 class의 목록
with open(train_data) as f:
    loaded_value = yaml.safe_load(f)
    all_child_names = loaded_value['names']
    print ('All child names', all_child_names)
# Childeren Target Setting

target_child_name = "face" # 우리가 찾으려는 아이의 이름
target_child_id = all_child_names.index(target_child_name) # 이름을 컴퓨터가 읽을 수 있는 index로 변환

# Camera Target Setting
error_x = 0
allowed_error = 0.1

model = YOLO('runs/detect/train57_version7/best.pt')

if train_mode:
    history = model.train(data = train_data, imgsz = image_size, epochs = epoch, batch = batch_size)
else:
    model = YOLO('runs/detect/train57_version7/best.pt')




cam = ai.Camera(camera_target)


while True:
    img = cam.read() # 카메라 열기
    print (img)
    pred_result = list(model(img)) # 예측된 결과 모두 불러오기

    get_result_img = pred_result[0].plot() # 예측된 결과 이미지 그리기
    get_boxes = pred_result[0].boxes # 예측된 결과의 박스 좌표 가져오기

    for i, box in enumerate(get_boxes): # 모든 박스 불러오기
        print (box.cls) # 박스의 클래스 출력
        if box.cls == target_child_id:
            print (box.xywhn)
            center_x, center_y, width, height = list(box.xywhn[0])
            print ('{name} childeren found'.format(name = target_child_name), center_x, center_y, width, height)
            print ('Robot moving')
            error_x = 0.5 - center_x #목표값 - 현재 값
            
            if abs(error_x) <= allowed_error:
                print ("{name} childeren infront of me".format(name = target_child_name))
                #Robot Stop
            break

    cv2.imshow("YOLOv8 Inference", get_result_img)
    if cam.check_key() == 'esc': break

2023-06-10 16:54:51.815122: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2023-06-10 16:54:51.884351: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2023-06-10 16:54:51.885754: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-06-10 16:54:53.508679: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


SystemExit: 

/home/yumjunstar/.local/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3516: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)


In [1]:
import numpy as np
import cv2
import glob
import roboidai as ai

camera_target = 'ip0'
cam = ai.Camera(camera_target)
img = cam.read()

while img is None:
    img = cam.read()
while True:

    print (type(img))
    print (img.ndim)
    print (img.shape)
    print (img.size)
    print (img.dtype)
    print (img.itemsize)

    cam.show(img)
    # try:
    #     cv2.imshow("Original img", img)
    # except Exception as e:
    #     print ('Exception', e)
# termination criteria
criteria = (cv2.TERM_CRITERIA_EPS + cv2.TERM_CRITERIA_MAX_ITER, 30, 0.001)
# prepare object points, like (0,0,0), (1,0,0), (2,0,0) ....,(6,5,0)
objp = np.zeros((6*7,3), np.float32)
objp[:,:2] = np.mgrid[0:7,0:6].T.reshape(-1,2)
# Arrays to store object points and image points from all the images.
objpoints = [] # 3d point in real world space
imgpoints = [] # 2d points in image plane.
images = glob.glob('./data/chess/*.jpg')



for fname in images:
    img = cv2.imread(fname)
    gray = cv2.cvtColor(img,cv2.COLOR_BGR2GRAY)
    # Find the chess board corners
    ret, corners = cv2.findChessboardCorners(gray, (7,6),None)
    # If found, add object points, image points (after refining them)
    if ret == True:
        objpoints.append(objp)
        corners2 = cv2.cornerSubPix(gray,corners,(11,11),(-1,-1),criteria)
        imgpoints.append(corners2)
        # Draw and display the corners
        img = cv2.drawChessboardCorners(img, (7,6), corners2,ret)
        cv2.imshow('img',img)
        cv2.waitKey(500)
cv2.destroyAllWindows()

2023-06-10 17:05:25.202761: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2023-06-10 17:05:25.296946: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2023-06-10 17:05:25.302237: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-06-10 17:05:26.994310: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


scanning ip camera...
scanning completed
<class 'numpy.ndarray'>
3
(320, 640, 3)
614400
uint8
1
<class 'numpy.ndarray'>
3
(320, 640, 3)
614400
uint8
1
<class 'numpy.ndarray'>
3
(320, 640, 3)
614400
uint8
1
<class 'numpy.ndarray'>
3
(320, 640, 3)
614400
uint8
1
<class 'numpy.ndarray'>
3
(320, 640, 3)
614400
uint8
1
<class 'numpy.ndarray'>
3
(320, 640, 3)
614400
uint8
1
<class 'numpy.ndarray'>
3
(320, 640, 3)
614400
uint8
1
<class 'numpy.ndarray'>
3
(320, 640, 3)
614400
uint8
1
<class 'numpy.ndarray'>
3
(320, 640, 3)
614400
uint8
1
<class 'numpy.ndarray'>
3
(320, 640, 3)
614400
uint8
1
<class 'numpy.ndarray'>
3
(320, 640, 3)
614400
uint8
1
<class 'numpy.ndarray'>
3
(320, 640, 3)
614400
uint8
1
<class 'numpy.ndarray'>
3
(320, 640, 3)
614400
uint8
1
<class 'numpy.ndarray'>
3
(320, 640, 3)
614400
uint8
1
<class 'numpy.ndarray'>
3
(320, 640, 3)
614400
uint8
1
<class 'numpy.ndarray'>
3
(320, 640, 3)
614400
uint8
1
<class 'numpy.ndarray'>
3
(320, 640, 3)
614400
uint8
1
<class 'numpy.ndarray'>


SystemExit: 

/home/yumjunstar/.local/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3516: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)


: 